# Import Packages

In [2]:
# NLP Packages
import nltk
from nltk.corpus import wordnet
# nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer
import re 
import string
import spacy
from spacy.lang.en.stop_words import STOP_WORDS
from spacy.lang.en import English

from sklearn.decomposition import LatentDirichletAllocation, TruncatedSVD 
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.manifold import TSNE
from sklearn.model_selection import GridSearchCV, train_test_split

In [3]:
# Plotting tools
import pyLDAvis
import pyLDAvis.sklearn

import plotly.offline as py
import plotly.graph_objects as go
py.init_notebook_mode(connected=False)

In [4]:
# Standard Python packages
import numpy as np
import pandas as pd

# Read in Data

In [9]:
# Load from file
import pickle
with open('final_raw_data.pkl', 'rb') as file:
    talk_df = pickle.load(file)

In [10]:
talk_df.head()

date               speaker  \
0  Jan 2020       Ipsita Dasgupta   
1  Jan 2020          Rod Phillips   
2  Jan 2020          Pat Mitchell   
3  Dec 2019      Cara E. Yar Khan   
4  Dec 2019  Valorie Kondos Field   

                                               title  \
0  To challenge the status quo, find a "co-conspi...   
1                         A brief history of alcohol   
2           Dangerous times call for dangerous women   
3     The beautiful balance between courage and fear   
4           Why winning doesn't always equal success   

                                                 url length  \
0  /talks/ipsita_dasgupta_to_challenge_the_status...  11:03   
1     /talks/rod_phillips_a_brief_history_of_alcohol   4:56   
2  /talks/pat_mitchell_dangerous_times_call_for_d...  17:14   
3  /talks/cara_e_yar_khan_the_beautiful_balance_b...   9:55   
4  /talks/valorie_kondos_field_why_winning_doesn_...  15:49   

                                                summ  \
0  In a complex and changing world, how can we ma...   
1  Nobody knows exactly when humans began to crea...   
2  Pat Mitchell has nothing left to prove and muc...   
3  After being diagnosed with a rare genetic cond...   
4  Valorie Kondos Field knows a lot about winning...   

                                                tags     views  \
0  [innovation, collaboration, society, social ch...  599446.0   
1  [TED-Ed, education, animation, history, cultur...  501290.0   
2  [women, women in business, community, activism...  461705.0   
3  [fear, personal growth, health, life, humanity...  880662.0   
4  [success, sports, leadership, empathy, compass...  956498.0   

                                          transcript date_recorded  \
0  So I've been thinking about how to explain thi...    2019-09-24   
1  This chimpanzee stumbles across a windfall of ...    2020-01-02   
2  Recently, I've been declaring to anyone who wo...    2019-12-04   
3  When we're young, we're innocently brave, and ...    2019-12-04   
4  OK, I have a question for all of us. You ready...    2019-12-04   

  upload_date                            occupation  \
0  2020-01-02  Business executive, "co-conspirator"   
1  2020-01-02                                   NaN   
2  2020-01-02                       Dangerous woman   
3  2019-12-23  Human rights and disability activist   
4  2019-12-20                      Gymnastics coach   

                                                 bio  comments  \
0  Ipsita Dasgupta drives the consumption of ente...       7.0   
1                                                NaN       NaN   
2  Pat Mitchell is a lifelong advocate for women ...      14.0   
3  Cara E. Yar Khan is an international human rig...      17.0   
4  Valorie Kondos Field is the retired head coach...      18.0   

            event  duration  tag_len  transcript_cc  transcript_wc  
0  TED@BCG Mumbai       663       10          10379           1874  
1          TED-Ed       296        7           4107            649  
2   TEDWomen 2019      1034       12          10691           1884  
3   TEDWomen 2019       595        7           7658           1373  
4   TEDWomen 2019       949       11          10161           1793

In [11]:
talk_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3646 entries, 0 to 3648
Data columns (total 19 columns):
date             3646 non-null object
speaker          3646 non-null object
title            3646 non-null object
url              3646 non-null object
length           3646 non-null object
summ             3646 non-null object
tags             3646 non-null object
views            3607 non-null float64
transcript       3646 non-null object
date_recorded    3557 non-null datetime64[ns]
upload_date      3557 non-null datetime64[ns]
occupation       3223 non-null object
bio              3235 non-null object
comments         3008 non-null float64
event            3646 non-null object
duration         3646 non-null int64
tag_len          3646 non-null int64
transcript_cc    3646 non-null int64
transcript_wc    3646 non-null int64
dtypes: datetime64[ns](2), float64(2), int64(4), object(11)
memory usage: 569.7+ KB


# Train, Test, Split

In [12]:
X = talk_df.transcript # Independent Variable
y = talk_df.views      # Dependent Variable

In [13]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42)

In [21]:
X_train.to_csv('train_data.csv', header = True)

In [22]:
X_test.to_csv('test_data.csv', header = True)

In [25]:
X_train.shape

(2916,)

In [26]:
X_test.shape

(730,)

# Tokenize Transcripts

## Helper Functions

In [14]:
# Adds in space between punctuation and words
def add_spaces(text):
    
    # Find instances of punctuation followed by two letters
    cleanr = re.compile('[.!?,;][A-Za-z][A-Za-z]')
    no_spaces = re.findall(cleanr, text)

    if len(no_spaces) > 0:
        for match in no_spaces:
            punc = match[0] # get the punctuation mark
            word = match[1:] # get the start of the word
            
            if punc != '?':
                text = re.sub(f"{match}", f"{punc} {word}", text)
            
            # Special case of ?, cannot be escaped
            else:
                text = re.sub(f"[?]{word}", f"? {word}", text)
    
    return text

In [15]:
# Handles numbers with 1) commas, 2) before hyphens, 3) in places (1st, 2nd, 3rd, etc.)

def handle_numbers(text):
    
    # Handle numbers with commas
    clean_commas = re.compile('[0-9]+,[0-9][0-9][0-9]')
    num_commas = re.findall(clean_commas, text)

    if len(num_commas) > 0:
        for match in num_commas:
            replace_str = match.replace(',', '')
            text = re.sub(f"{match}", f"{replace_str}", text)
    
    # Handle numbers with hyphens
    clean_numbers = re.compile('[0-9]+-')
    numbers = re.findall(clean_numbers, text)

    if len(numbers) > 0:
        for match in numbers:
            text = re.sub(f"{match}", "# ", text)
    
    # Handle 1st, 2nd, 3rd with hyphens
    text = text.replace('1st-', '1st ').replace('2nd-', '2nd ').replace('3rd-', '3rd ')
    
    # Handle -th with hyphens
    clean_places = re.compile('[0-9]th-')
    places_hyphen = re.findall(clean_places, text)

    if len(places_hyphen) > 0:
        for match in places_hyphen:
            text = re.sub(f"{match}", f"{match[:-1]} ", text)
    
    return text

In [16]:
def handle_parentheses(text):
    
    # Add spaces before and after parentheses
    text = text.replace(')', ')\n').replace('(', ' (')
    
    # Find all parenthetical phrases
    clean_parentheses = re.compile('\(.*\)')
    parentheses = re.findall(clean_parentheses, text)
    
    if len(parentheses) > 0:
        for match in parentheses:
            try:
                text = re.sub(f'{match}', ' ', text)
            except:
                text = re.sub('(Applause.)', '. ', text)
                text = re.sub('(Laughter.)', '. ', text)
                text = re.sub('(Music.)', '. ', text)
                text = text.replace('(Applause.', '. ')
                text = text.replace('(Laughter.', '. ')
                text = text.replace('(Music.', '. ')
                text = re.sub('\(|\)', '. ', text)
    
    text = text.replace('( )', '')
    
    return ' '.join(text.split())

<>:7: DeprecationWarning:

invalid escape sequence \(

<>:21: DeprecationWarning:

invalid escape sequence \(

<>:7: DeprecationWarning:

invalid escape sequence \(

<>:21: DeprecationWarning:

invalid escape sequence \(

<>:7: DeprecationWarning:

invalid escape sequence \(

<>:21: DeprecationWarning:

invalid escape sequence \(

<ipython-input-16-e1e376dc5729>:7: DeprecationWarning:

invalid escape sequence \(

<ipython-input-16-e1e376dc5729>:21: DeprecationWarning:

invalid escape sequence \(



## Stop Words & Punctuation

In [17]:
# Create our list of punctuation marks
punctuations = string.punctuation

# Create our list of stopwords
nlp = spacy.load('en_core_web_sm')
stop_words = spacy.lang.en.stop_words.STOP_WORDS

# Add some more stopwords
stop_words = list(stop_words)
stop_words.extend(['yeah', 'ya', 'ah', 'um', 'oh', 'actually', 'literally', 'like', 's', 'applause'])

## Tokenization Function

In [18]:
# Initialize lemmatizer
lemmatizer = WordNetLemmatizer()

In [19]:
def spacy_tokenizer(text):
    
    # Remove .., ..., ....
    no_ellipses = text.replace('....', '').replace('...', '').replace('..','').replace('…', '')
    
    # Remove parenthetical phrases
    no_parentheses = handle_parentheses(no_ellipses)
    
    # Add missing spaces after punctuation
    with_spaces = add_spaces(no_parentheses)
    
    # Handle numbers with commas
    clean_numbers = handle_numbers(with_spaces)
    
    # Remove quotation marks
    no_quotes = clean_numbers.replace('\"', ' ').replace('”', ' ').replace('’', '')
    
    # Address hyphenation issue -- need to revisit
    no_ism = no_quotes.replace('-ism', 'ism')
    no_dash = no_ism.replace('–', ' ').replace('—', ' ').replace('-', '')
    
    # Remove music notes
    no_notes = no_dash.replace('♪', '').replace('♫', '')
    
    # SPECIFIC RULE
    no_spec = no_notes.replace('R and D', 'research and development').replace('R & D', 'research and development')
    
    # Replace all whitespace with one space
    cleantext = ' '.join(no_spec.split())
    cleantext = cleantext.strip()
    
    # Creating our token object, which is used to create documents with linguistic annotations.
    # we disabled the parser and ner parts of the pipeline in order to speed up parsing
    mytokens = nlp(cleantext.lower(), disable=['parser', 'ner'])
    
    # Lemmatizing each token and converting each token into lowercase
    lemmas = []
    for word in mytokens:
        if word.pos_ == 'NOUN':
            lemmas.append(lemmatizer.lemmatize(word.text.lower().strip(), wordnet.NOUN))
        elif word.pos_ == 'VERB':
            lemmas.append(lemmatizer.lemmatize(word.text.lower().strip(), wordnet.VERB))
        elif word.pos_ == 'ADV':
            lemmas.append(lemmatizer.lemmatize(word.text.lower().strip(), wordnet.ADV))
        elif word.pos_ == 'ADJ':
            lemmas.append(lemmatizer.lemmatize(word.text.lower().strip(), wordnet.ADJ))

    lemmas = [word for word in lemmas if word not in stop_words and word not in punctuations]
    
    # return preprocessed list of tokens
    return lemmas

# Create Tokens For Training Set

In [20]:
X_train_lemmas = X_train.apply(spacy_tokenizer)

In [19]:
X_train_lemmas

2987    [bug, lover, childhood, way, late, bachelor, m...
2285    [ancient, great, idea, universe, simple, mind,...
1802    [let, south, south, direction, way, kilometer,...
2163    [cool, thing, game, throne, inhabitant, real, ...
1583    [tell, parent, gay, thing, bring, mind, sexual...
1816    [expose, tear, gas, tear, gas, sorry, hear, kn...
2354    [good, sex, fade, couple, continue, love, good...
1361    [funny, thing, forget, mother, day, tell, stor...
576     [childhood, memory, stand, rest, time, brave, ...
3178    [writer, journalist, insanely, curious, person...
2417    [today, talk, sketch, thing, electrical, engin...
1475    [talk, today, story, condition, believe, possi...
3510    [thing, hold, want, start, today, talk, struct...
528     [way, tell, story, naturally, change, define, ...
176     [climate, change, hear, nearly, psychological,...
3635    [excited, today, stuff, ready, come, lab, glad...
422     [believe, world, good, place, try, design, wor...
680     [socia

In [44]:
X_train_gensim = list(X_train_lemmas)

In [47]:
X_train_gensim[0]

['bug',
 'lover',
 'childhood',
 'way',
 'late',
 'bachelor',
 'major',
 'zoology',
 'kind',
 'fell',
 'love',
 'bug',
 'zoology',
 'course',
 'discipline',
 'entomology',
 'science',
 'insect',
 'think',
 'practical',
 'help',
 'science',
 'entomology',
 'world',
 'plant',
 'protection',
 'plant',
 'protection',
 'insect',
 'bad',
 'bug',
 'plant',
 'protection',
 'come',
 'discipline',
 'biological',
 'pest',
 'control',
 'define',
 'use',
 'live',
 'organism',
 'reduce',
 'population',
 'noxious',
 'plant',
 'pest',
 'discipline',
 'plant',
 'protection',
 'aim',
 'reduction',
 'chemical',
 'biological',
 'pest',
 'control',
 'way',
 'good',
 'bug',
 'talk',
 'exist',
 'world',
 'thousand',
 'thousand',
 'year',
 'long',
 'long',
 'time',
 'year',
 'people',
 'start',
 'people',
 'know',
 'exploit',
 'use',
 'biological',
 'control',
 'phenomenon',
 'fact',
 'natural',
 'control',
 'phenomenon',
 'need',
 'biological',
 'control',
 'phenomenon',
 'backyard',
 'magnify',
 'glass',
 '

# Gensim

In [333]:
from gensim.models import CoherenceModel, LdaModel, HdpModel
from gensim.corpora import Dictionary

In [334]:
dictionary = Dictionary(X_train_gensim)
dictionary.filter_extremes(no_below=5, no_above=0.7)
corpus = [dictionary.doc2bow(text) for text in X_train_gensim]

In [337]:
test_gensim_lda = LdaModel(corpus=corpus, id2word=dictionary, iterations=25, num_topics=15)

In [338]:
test_gensim_cm = CoherenceModel(model=test_gensim_lda, texts=X_train_gensim, dictionary=dictionary, coherence='c_v')

In [339]:
test_gensim_cm.get_coherence()

0.25898325206422596

# SKLearn

## Create String of Tokens

In [21]:
def get_new_transcript(lemmas):
    transcript = ''
    for lemma in lemmas:
        transcript += lemma.strip() + ' '
    return transcript.strip()

In [22]:
X_train_tok_trans = X_train_lemmas.apply(get_new_transcript)

In [20]:
X_train_tok_trans

2987    bug lover childhood way late bachelor major zo...
2285    ancient great idea universe simple mind need e...
1802    let south south direction way kilometer room c...
2163    cool thing game throne inhabitant real languag...
1583    tell parent gay thing bring mind sexual orient...
1816    expose tear gas tear gas sorry hear know toxic...
2354    good sex fade couple continue love good intima...
1361    funny thing forget mother day tell story compl...
576     childhood memory stand rest time brave parent ...
3178    writer journalist insanely curious person year...
2417    today talk sketch thing electrical engineer me...
1475    talk today story condition believe possible st...
3510    thing hold want start today talk structure pol...
528     way tell story naturally change define rule tr...
176     climate change hear nearly psychological impac...
3635    excited today stuff ready come lab glad guy pe...
422     believe world good place try design world star...
680     social

# Vectorize Tokens

## CountVectorizer

In [23]:
cv = CountVectorizer(max_df = 0.7, min_df = 4)

In [24]:
dtm_cv_train = cv.fit_transform(X_train_tok_trans)

In [18]:
len(cv.get_feature_names())

15146

## TfidfVectorizer

In [30]:
tfidf = TfidfVectorizer(max_features = 1000, max_df = 0.6, min_df = 4)

In [31]:
dtm_tfidf_train = tfidf.fit_transform(X_train_tok_trans)

# Latent Semantic Analysis (Truncated SVD)

In [24]:
# Returns dataframe of top n words
def topic_top_words(model, feature_names, n):
    topic_word_dict = {}
    
    for topic_idx, topic in enumerate(model.components_):
        
        topic_word_dict['Topic ' + str(topic_idx + 1)] = [feature_names[i] for i in topic.argsort()[:-n - 1:-1]]
    
    return pd.DataFrame.from_dict(topic_word_dict, orient='index', columns = range(1, n + 1))

## CountVectorizer

In [33]:
lsa_cv = TruncatedSVD(n_components = 20, algorithm = 'randomized', n_iter = 3, random_state = 42)

In [34]:
lsa_cv.fit(dtm_cv_train)

TruncatedSVD(algorithm='randomized', n_components=20, n_iter=3, random_state=42,
             tol=0.0)

In [340]:
topic_top_words(lsa_cv, cv.get_feature_names(), 20)

NameError: name 'lsa_cv' is not defined

## TfidfVectorizer

In [36]:
lsa_tfidf = TruncatedSVD(n_components = 20, algorithm = 'randomized', n_iter = 3, random_state = 42)

In [37]:
lsa_tfidf.fit(dtm_tfidf_train)

TruncatedSVD(algorithm='randomized', n_components=20, n_iter=3, random_state=42,
             tol=0.0)

# LDA (n = 25)

In [25]:
lda_cv_25 = LatentDirichletAllocation(n_components=25,           # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=42,          # Random state
                                      batch_size=100,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      )

In [26]:
lda_cv_25.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=25, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [40]:
lda_cv_25.score(dtm_cv_train)

-12601995.233764943

In [41]:
lda_cv_25.perplexity(dtm_cv_train)

2716.9177544742574

In [341]:
topic_top_words(lda_cv_25, cv.get_feature_names(), 10)

1           2           3           4           5   \
Topic 0        brain       human        tell        kind         try   
Topic 1        light      energy       earth      planet       space   
Topic 2         cell       brain     disease      animal        body   
Topic 3    political   democracy        vote    election  government   
Topic 4      country     percent      change     company     problem   
Topic 5          day       story         kid      little        tell   
Topic 6         data  technology    computer       robot     machine   
Topic 7        dandy     emperor   community      change     problem   
Topic 8    algorithm       score  programmer   rectangle        data   
Topic 9     language        word       write        book       speak   
Topic 10   satellite      rocket       space       orbit      launch   
Topic 11       music       sound        food        play        hear   
Topic 12      female        male      insect      beetle       sperm   
Topic 13  concussion    football        ping        harp       koran   
Topic 14        city      design    building       build       place   
Topic 15        pain        fire       flame       place   emotional   
Topic 16      cancer      health      doctor   treatment    medicine   
Topic 17       woman       child        life      family         men   
Topic 18        baby         egg         bee      colony        milk   
Topic 19       image        body       color      object        face   
Topic 20       wrist  locomotion          tk  salamander        hump   
Topic 21      choice      choose       olive  lefthanded    rational   
Topic 22         kit        rape         kid        help      school   
Topic 23       water         ice         sea       ocean    mountain   
Topic 24       drone      weapon        bomb     fiction      firing   

                   6           7               8            9             10  
Topic 0          talk        life        question    different           let  
Topic 1      universe         car             big         life         small  
Topic 2         human     patient          system       specie           new  
Topic 3      politics      medium         citizen          ant         party  
Topic 4           new       money           today       happen           lot  
Topic 5          love        life             try       school         great  
Topic 6   information    internet           build        video         phone  
Topic 7          life        city             job   government           day  
Topic 8    prevalence        math           match      fitness          area  
Topic 9        letter       learn        sentence      english       speaker  
Topic 10   spacecraft  subsurface        shipping        earth      location  
Topic 11        voice         eat          listen         song    instrument  
Topic 12         dung       penis             kit         cork  reproduction  
Topic 13          tee       costa          bouncy        reply        castle  
Topic 14         tree       water           space        plant          grow  
Topic 15         idea       light            heat     molecule           gas  
Topic 16        tumor     surgery          breast     diagnose     radiation  
Topic 17         tell        girl          mother         talk         young  
Topic 18          fly         bat           plant          lie        flower  
Topic 19       create        skin          beauty        paper     structure  
Topic 20          han     rosling  neurobiologist     lowlevel          game  
Topic 21          car    ideology          chance  righthanded        casino  
Topic 22        image      victim           black          lot       problem  
Topic 23         cave        foot            cold         snow          pole  
Topic 24          edi     fascism     nationalism      fascist    neoliberal

# Latent Dirichlet Allocation (n = 20)

In [27]:
lda_cv = LatentDirichletAllocation(n_components=20,           # Number of topics
                                   max_iter=10,               # Max learning iterations
                                   learning_method='online',   
                                   random_state=42,          # Random state
                                   batch_size=100,            # n docs in each learning iter
                                   evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                   n_jobs = -1,               # Use all available CPUs
                                   )

In [28]:
lda_cv.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=20, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [343]:
topic_top_words(lda_cv, cv.get_feature_names(), 10)

1           2           3          4            5   \
Topic 0          life        tell       brain       talk         feel   
Topic 1         light      energy       earth     planet     universe   
Topic 2         brain       human  technology   computer       system   
Topic 3     political  government      medium  democracy         vote   
Topic 4       country     percent     company     change      problem   
Topic 5        little         day       story       tell         love   
Topic 6      internet         web      online    privacy         site   
Topic 7   interviewer         edi     emperor      dandy  illusionist   
Topic 8       patient      health      cancer    disease       doctor   
Topic 9        school     student    language      learn          kid   
Topic 10    satellite       space       orbit     launch      climber   
Topic 11         food         eat       plant     animal        water   
Topic 12       female       sperm       penis       cork        hater   
Topic 13        music       sound        play      voice         hear   
Topic 14         city      design    building      build        place   
Topic 15         idea       place        pain       fire      problem   
Topic 16    staircase    employer  internship   seedling        stair   
Topic 17        woman       child      family        men         girl   
Topic 18         face         bee      colony     facial          bat   
Topic 19         cell        body       blood      heart         drug   

                  6           7           8              9             10  
Topic 0        human        mean      happen            try           ask  
Topic 1        space       water        life            big        carbon  
Topic 2        robot         new   different           data          kind  
Topic 3        power    election     country       politics       citizen  
Topic 4          new         lot       money          today        happen  
Topic 5         kind         try        life          great          talk  
Topic 6        email        data     website            ork  surveillance  
Topic 7      orchard       chant  wilderness         baking           bce  
Topic 8         care     medical   treatment       hospital      medicine  
Topic 9         word     teacher       teach           book     education  
Topic 10  locomotion  spacecraft  subsurface  constellation       highway  
Topic 11        grow      farmer       virus        disease       vaccine  
Topic 12      squeal         mta    denounce     disapprove  insemination  
Topic 13        song      listen        sing     instrument         noise  
Topic 14       space     project        tree           live        create  
Topic 15    business         gas      create        protect         flame  
Topic 16       cedar     reentry  dumbstruck           weep       relearn  
Topic 17        life        tell      mother          young           war  
Topic 18         egg      flower       green         insect         smile  
Topic 19        skin    molecule       organ         tissue        muscle

In [146]:
# Helper functions for dtm style
def color_green(val):
    color = 'green' if val > .1 else 'black'
    return 'color: {col}'.format(col=color)

def make_bold(val):
    weight = 700 if val > .1 else 400
    return 'font-weight: {weight}'.format(weight=weight)


In [236]:
def print_dtm(topic_model, dtm):
    # Create Document - Topic Matrix
    output = topic_model.transform(dtm)

    # column names
    topicnames = ["Topic" + str(i) for i in range(topic_model.n_components)]

    # index names
    docnames = ["Doc" + str(i) for i in range(dtm.shape[0])]

    # Make the pandas dataframe
    df_document_topic = pd.DataFrame(output, columns=topicnames, index=docnames)

    # Get dominant topic for each document
    dominant_topic = np.argmax(df_document_topic.values, axis=1)

    # Get next dominant topic for each document
    sorted_topics = np.argsort(df_document_topic.values, axis = 1)
    secondary_topic = [doc[-2] for doc in sorted_topics]

    # Get third dominant topic for each document
    tertiary_topic = [doc[-3] for doc in sorted_topics]

    df_document_topic['dominant_topic'] = dominant_topic
    df_document_topic['secondary_topic'] = secondary_topic
    df_document_topic['tertiary_topic'] = tertiary_topic
    
    return df_document_topic

In [237]:
lda_cv_table = print_dtm(lda_cv, dtm_cv_train)

In [239]:
lda_cv_table.head(100).style.applymap(color_green).applymap(make_bold) # apply style

In [168]:
unique, counts = np.unique(dominant_topic, return_counts=True)
print(np.asarray((unique, counts)).T)

[[  0 561]
 [  1 186]
 [  2 475]
 [  3  16]
 [  4 684]
 [  5 562]
 [  6   1]
 [  9  41]
 [ 11  27]
 [ 13   7]
 [ 14 122]
 [ 17 216]
 [ 18   2]
 [ 19  16]]


In [169]:
unique, counts = np.unique(secondary_topic, return_counts=True)
print(np.asarray((unique, counts)).T)

[[  1 199]
 [  2 598]
 [  3  22]
 [  4 785]
 [  5 686]
 [  6   2]
 [  8   8]
 [  9  65]
 [ 11  36]
 [ 13  19]
 [ 14 136]
 [ 17 327]
 [ 18   4]
 [ 19  29]]


# LDA (n = 17)

In [29]:
lda_cv_17 = LatentDirichletAllocation(n_components=17,           # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=42,          # Random state
                                      batch_size=100,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      )

In [30]:
lda_cv_17.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=17, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [136]:
topic_top_words(lda_cv_17, cv.get_feature_names(), 15)

1        2          3          4           5           6   \
Topic 0        life     tell       talk      brain         try       human   
Topic 1       light   energy      earth     planet       space         car   
Topic 2        cell    brain      human      robot        body      system   
Topic 3   political   medium  democracy       vote  government    election   
Topic 4     country  percent     change      today        talk     problem   
Topic 5         day     life      story       tell        love      little   
Topic 6       woman      men        sex     female        male        girl   
Topic 7         edi  emperor     socket         tk    amputate  prosthesis   
Topic 8     company     data   business      money    computer      dollar   
Topic 9      school  student        kid   language       learn        game   
Topic 10  satellite    orbit      space     launch  subsurface  locomotion   
Topic 11       food      eat      plant     animal      farmer        grow   
Topic 12        ice      bee       cave     colony      insect         bat   
Topic 13      music    sound       play      voice        hear        song   
Topic 14     design     city   building      build       place     project   
Topic 15     fusion   helium    neutron     plasma     breeder     fission   
Topic 16     cancer    tumor     breast  treatment      doctor     disease   

                  7              8            9         10          11  \
Topic 0         kind           mean       happen  question        feel   
Topic 1          big       universe        water    little        kind   
Topic 2   technology            new    different    animal        able   
Topic 3     politics          power         news     party  journalist   
Topic 4       happen          child    community       new         let   
Topic 5         feel           talk        child      live      family   
Topic 6       sexual           body      partner       gay    violence   
Topic 7          com          dandy      amputee     leone     orchard   
Topic 8   technology       internet  information   product      market   
Topic 9         word           book      teacher     teach   education   
Topic 10  spacecraft  constellation     location   stutter     orbital   
Topic 11       smell           farm        waste       fee     produce   
Topic 12        snow         flower      glacier      pole  expedition   
Topic 13      listen          piece   instrument      sing         let   
Topic 14       space         create         kind      tree       water   
Topic 15     feynman   kilowatthour     reaction    cuddly    megawatt   
Topic 16      mother           baby      surgery   quantum      health   

                        12           13          14            15  
Topic 0                lot          let         ask     different  
Topic 1               life         mean         lot         small  
Topic 2             little      disease     machine        specie  
Topic 3            citizen     internet     twitter        social  
Topic 4                lot         mean        help        system  
Topic 5             friend         walk         ask           man  
Topic 6               talk       victim      desire         young  
Topic 7   unpredictability       sierra       gyrus      fusiform  
Topic 8                pay       create  innovation         value  
Topic 9               read        class       child         write  
Topic 10              junk       debris     traffic        refuel  
Topic 11              meat  agriculture       taste         sugar  
Topic 12              cold         foot     cricket         polar  
Topic 13              note        noise      record         video  
Topic 14               new         idea    material          live  
Topic 15             ripen        repel     dislike       uranium  
Topic 16          homeless    radiation    medicine  chemotherapy

# LDA (n = 16)

In [31]:
lda_cv_16 = LatentDirichletAllocation(n_components=16,           # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=42,          # Random state
                                      batch_size=100,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      )

In [32]:
lda_cv_16.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=16, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [139]:
topic_top_words(lda_cv_16, cv.get_feature_names(), 15)

1           2           3          4           5   \
Topic 0        brain       human        tell       life         try   
Topic 1        light      energy       earth     planet    universe   
Topic 2         cell       human       water     system        body   
Topic 3    political  government   democracy     medium        vote   
Topic 4      country     percent      change    company     problem   
Topic 5         life       woman         day       tell       story   
Topic 6          sex       woman      female       male         men   
Topic 7      emperor         edi  wilderness  cervantes       dandy   
Topic 8      patient      cancer      health    disease      doctor   
Topic 9     language        word        book       game       write   
Topic 10   satellite      launch       orbit      space  locomotion   
Topic 11        food       plant         eat     animal        grow   
Topic 12      police       crime      victim   violence    criminal   
Topic 13       music       sound        play      voice        hear   
Topic 14      design        city       build       kind       robot   
Topic 15  prosthesis      socket  amputation         tk    amputate   

                  6           7              8         9           10  \
Topic 0         kind   different         happen       let        talk   
Topic 1        space         big           life       car        star   
Topic 2   technology         new         animal      data      little   
Topic 3     election    politics    information  internet     citizen   
Topic 4       happen         new          today      talk         lot   
Topic 5         love       child            kid      talk        feel   
Topic 6       sexual        body            egg   partner       smell   
Topic 7     drowning       lance       landmine   orchard  government   
Topic 8    treatment    medicine        medical      care       tumor   
Topic 9         read    computer          learn   student     teacher   
Topic 10  subsurface  spacecraft  constellation   stutter        junk   
Topic 11      farmer        farm          waste     water         dog   
Topic 12      arrest     officer           case       bat        rape   
Topic 13        song       video         listen       let  instrument   
Topic 14    building        idea         create   project       space   
Topic 15     amputee       gyrus       fusiform     ankle        wisp   

                        11           12              13       14          15  
Topic 0           question          lot            feel     mean      little  
Topic 1             carbon         mean         climate     kind      little  
Topic 2               able    different          specie    ocean        life  
Topic 3              party   journalist           power     news     twitter  
Topic 4              money          let            mean   system         big  
Topic 5             family       school            live      ask      little  
Topic 6             desire      hormone          beetle   fusion       sperm  
Topic 7   unpredictability          kit             bce    lofty         job  
Topic 8             patent       breast           woman     cure   physician  
Topic 9             letter         page         example    teach         new  
Topic 10            debris    catherine  neurobiologist   refuel  propellant  
Topic 11            insect      produce     agriculture   specie        meat  
Topic 12            sexual  enforcement      harassment  convict    sentence  
Topic 13             piece         sing          record     note       noise  
Topic 14               new        place        material     sort      little  
Topic 15              pain         idea           place    flame      design

# LDA (n = 15)

In [33]:
lda_cv_15 = LatentDirichletAllocation(n_components=15,           # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=42,          # Random state
                                      batch_size=100,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      )

In [34]:
lda_cv_15.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=15, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [250]:
import pickle

In [281]:
# Save to lda model
pkl_filename = "lda_15.pkl"
with open(pkl_filename, 'wb') as file:
    pickle.dump(lda_cv_15, file)
    
# Save vectorizer
cv_filename = 'cv.pkl'
with open(cv_filename, 'wb') as file:
    pickle.dump(cv, file)

# Format Results of Document-Topic Matrix from LDA

In [272]:
lda_cv_15_table = print_dtm(lda_cv_15, dtm_cv_train)

In [242]:
lda_cv_15_table.head(100).style.applymap(color_green).applymap(make_bold)

In [153]:
X_train_df_lda_15 = pd.DataFrame(X_train)

In [158]:
len(X_train_df_lda_15)

2916

In [274]:
lda_cv_15_table.index = X_train_df_lda_15.index

In [273]:
lda_cv_15_table.columns = ['00_general', '01_science', '02_technology', '03_politics', '04_problems', 
                           '05_interpersonal', '06_AI', '07_miscellaneous', '08_healthcare', '09_linguistics/humanities', 
                           '10_space', '11_agriculture/nature', '12_gender/sexuality', '13_audio/visual', '14_urban planning/design', 
                           'dominant_topic', 'secondary_topic', 'tertiary_topic']

In [275]:
X_train_df_lda_top = pd.concat([X_train_df_lda_15, lda_cv_15_table], axis = 1)

In [276]:
X_train_df_lda_top.head()

transcript  00_general  \
2987  I'm a bug lover, myself — not from childhood, ...    0.232992   
2285  The ancient Greeks had a great idea: The unive...    0.000199   
1802  Let's go south. All of you are actually going ...    0.031970   
2163  To many, one of the coolest things about "Game...    0.114946   
1583  Jenni Chang: When I told my parents I was gay,...    0.037066   

      01_science  02_technology  03_politics  04_problems  05_interpersonal  \
2987    0.069121       0.449050     0.000093     0.023710          0.000093   
2285    0.990310       0.007103     0.000199     0.000199          0.000199   
1802    0.308662       0.000131     0.000131     0.273386          0.276192   
2163    0.000330       0.000330     0.000330     0.000330          0.114692   
1583    0.000126       0.000126     0.140017     0.343803          0.464657   

         06_AI  07_miscellaneous  08_healthcare  09_linguistics/humanities  \
2987  0.020657          0.000093       0.001590                   0.000093   
2285  0.000199          0.000199       0.000199                   0.000199   
1802  0.000131          0.000131       0.000131                   0.000131   
2163  0.000330          0.000330       0.000330                   0.766402   
1583  0.000126          0.000126       0.000126                   0.000126   

      10_space  11_agriculture/nature  12_gender/sexuality  13_audio/visual  \
2987  0.000093               0.151210             0.013717         0.000093   
2285  0.000199               0.000199             0.000199         0.000199   
1802  0.000131               0.000131             0.089755         0.000131   
2163  0.000330               0.000330             0.000330         0.000330   
1583  0.000126               0.000126             0.013202         0.000126   

      14_urban planning/design  dominant_topic  secondary_topic  \
2987                  0.037396               2                0   
2285                  0.000199               1                2   
1802                  0.018858               1                5   
2163                  0.000330               9                0   
1583                  0.000126               5                4   

      tertiary_topic  
2987              11  
2285               0  
1802               4  
2163               5  
1583               3

In [277]:
X_train_df_lda_top.to_csv('final_lda.csv')

In [308]:
topics_df = pd.concat([X_train_df_lda_top, talk_df[['speaker', 'title', 'summ', 'comments', 'views', 'date_recorded', 'upload_date', 'duration', 'tag_len', 'occupation', 'bio']]], axis=1, join='inner')

In [322]:
topics_df = pd.concat([X_train_df_lda_top, talk_event], axis = 1, join = 'inner')

In [323]:
topics_df.head()

transcript  00_general  \
2987  I'm a bug lover, myself — not from childhood, ...    0.232992   
2285  The ancient Greeks had a great idea: The unive...    0.000199   
1802  Let's go south. All of you are actually going ...    0.031970   
2163  To many, one of the coolest things about "Game...    0.114946   
1583  Jenni Chang: When I told my parents I was gay,...    0.037066   

      01_science  02_technology  03_politics  04_problems  05_interpersonal  \
2987    0.069121       0.449050     0.000093     0.023710          0.000093   
2285    0.990310       0.007103     0.000199     0.000199          0.000199   
1802    0.308662       0.000131     0.000131     0.273386          0.276192   
2163    0.000330       0.000330     0.000330     0.000330          0.114692   
1583    0.000126       0.000126     0.140017     0.343803          0.464657   

         06_AI  07_miscellaneous  08_healthcare  09_linguistics/humanities  \
2987  0.020657          0.000093       0.001590                   0.000093   
2285  0.000199          0.000199       0.000199                   0.000199   
1802  0.000131          0.000131       0.000131                   0.000131   
2163  0.000330          0.000330       0.000330                   0.766402   
1583  0.000126          0.000126       0.000126                   0.000126   

      10_space  11_agriculture/nature  12_gender/sexuality  13_audio/visual  \
2987  0.000093               0.151210             0.013717         0.000093   
2285  0.000199               0.000199             0.000199         0.000199   
1802  0.000131               0.000131             0.089755         0.000131   
2163  0.000330               0.000330             0.000330         0.000330   
1583  0.000126               0.000126             0.013202         0.000126   

      14_urban planning/design  dominant_topic  secondary_topic  \
2987                  0.037396               2                0   
2285                  0.000199               1                2   
1802                  0.018858               1                5   
2163                  0.000330               9                0   
1583                  0.000126               5                4   

      tertiary_topic             event  
2987              11           TED2012  
2285               0      TED@Unilever  
1802               4  TEDxBeaconStreet  
2163               5           TED2014  
1583               3            TED-Ed

In [324]:
topics_df.to_csv('train_data_with_topics.csv')

In [303]:
topic_top_words(lda_cv_15, cv.get_feature_names(), 50).to_csv('lda_15_topics_words.csv')

In [304]:
topic_top_words(lda_cv_15, cv.get_feature_names(), 50)

1           2         3           4        5             6   \
Topic 0        life        tell     brain       human     talk          feel   
Topic 1       light      energy     earth      planet    space      universe   
Topic 2        cell       brain     human  technology   system     different   
Topic 3   political  government     power      medium      war     democracy   
Topic 4     country     percent    change     company  problem           new   
Topic 5         day        tell     story        life     love        little   
Topic 6       robot     machine  computer        game    build  intelligence   
Topic 7      socket          tk  amputate  prosthesis  amputee         dandy   
Topic 8      cancer     patient    health     disease   doctor      medicine   
Topic 9    language        word      book       write     read        letter   
Topic 10  satellite      rocket     orbit      launch    space    spacecraft   
Topic 11       food         eat     plant      farmer   animal          grow   
Topic 12      woman         men       sex      female     male        sexual   
Topic 13      music       sound      play       voice     hear          song   
Topic 14       city      design  building       build    place         space   

                  7         8              9           10  ...          41  \
Topic 0   experience     study            ask      person  ...        love   
Topic 1          big     water            car        life  ...     problem   
Topic 2          new      data         little        body  ...        area   
Topic 3      country      vote       internet    politics  ...      change   
Topic 4         talk     today            lot      happen  ...       build   
Topic 5          kid      talk           feel         try  ...      family   
Topic 6          leg   control            ant         car  ...        goal   
Topic 7        leone    sierra        blister     emperor  ...         new   
Topic 8      medical     tumor      treatment     surgery  ...  metastasis   
Topic 9        learn     speak        example   different  ...     culture   
Topic 10  subsurface  shipping  constellation    location  ...  monitoring   
Topic 11        farm     waste          smell       water  ...      supply   
Topic 12      victim       ice         colony    violence  ...    survivor   
Topic 13      listen      sing            let  instrument  ...       audio   
Topic 14        tree     water        project      create  ...        soil   

               42           43         44          45          46          47  \
Topic 0    answer       reason  attention       point        hand      friend   
Topic 1      mile          new       fact         bit      matter       place   
Topic 2       bit          dna      ocean      simple        mean       blood   
Topic 3      view     violence       fact   religious   terrorist      nation   
Topic 4       pay       future      value  technology     example         try   
Topic 5      book         help    realize        hear       stand    remember   
Topic 6      send        wheel   password  autonomous         fun        user   
Topic 7    sector       happen     decade       young         lot    economic   
Topic 8   ovarian        cause        bmi  pollinator    survival        flop   
Topic 9    phrase     spelling     writer       spell      common     history   
Topic 10  cleanup  mountaineer      quota      rumble       strew  unofficial   
Topic 11   planet    chocolate       land      coffee  production   vegetable   
Topic 12   vagina    pheromone     mating      evolve     puberty     genital   
Topic 13  concert       change      radio         bit   frequency  experience   
Topic 14  process    different      river         lot     century       small   

                 48          49          50  
Topic 0   important       heart      second  
Topic 1       point       ocean    particle  
Topic 2        form   structure        type  
Topic 

## Test on testing set

In [264]:
X_test_lemmas = X_test.apply(spacy_tokenizer) # Get test sets lemmas

In [265]:
X_test_tok_trans = X_test_lemmas.apply(get_new_transcript) # Get test sets new transcript

In [266]:
dtm_cv_test = cv.transform(X_test_tok_trans) # Get vectorized data

In [283]:
lda_cv_15_table_test = print_dtm(lda_cv_15, dtm_cv_test) # Apply lda and get results

In [285]:
lda_cv_15_table_test.columns = lda_cv_15_table.columns

In [327]:
lda_cv_15_table_test.index = X_test.index
X_test_df_lda_top = pd.concat([X_test, lda_cv_15_table_test], axis = 1, join = 'inner')

In [328]:
topics_test_df = pd.concat([X_test_df_lda_top, talk_df[['speaker', 'title', 'summ', 'comments', 'views', 'date_recorded', 'upload_date', 'duration', 'tags', 'tag_len', 'occupation', 'bio']]], axis=1, join='inner')

In [329]:
topics_test_df = pd.concat([topics_test_df, talk_event], axis = 1, join = 'inner')

In [350]:
topics_test_df

transcript  00_general  \
415   My subject is the future of life on Earth. Thi...    0.142867   
2930  I'm going to have a pretty simple idea that I'...    0.016962   
3197  I have a very difficult task. I'm a spectrosco...    0.000097   
298   Black holes are among the most destructive obj...    0.026053   
1875  I have the feeling that we can all agree that ...    0.042291   
2730  Ladies and gentlemen, gather around. I would l...    0.058451   
32    Corn currently accounts for more than one tent...    0.032942   
2866  Mark Zuckerberg, a journalist was asking him a...    0.010824   
2632  You know, I had a real rough time in school wi...    0.005304   
2900  There's a beautiful statement on the screen th...    0.044135   
657   When is seeing not believing? A couple years a...    0.047015   
2447  Five years ago, I experienced a bit of what it...    0.168953   
2966  Hello. My name is Birke Baehr, and I'm 11 year...    0.000244   
2513  So let me start by taking you back, back into ...    0.078858   
1832  I'm a lifelong traveler. Even as a little kid,...    0.127606   
1044  I recently read about what the young generatio...    0.083134   
2045  Our story is about a girl named Iris. Iris is ...    0.236913   
1074  These are some photos of me volunteering in a ...    0.176296   
897   You may know this feeling: you wake up to mult...    0.181027   
3234  Because of what I'm about to say, I really sho...    0.036358   
1206  What if I told you there was a new technology ...    0.251151   
3015  Well, that's kind of an obvious statement up t...    0.021344   
315   These are sequences from a play called "The Le...    0.029103   
461   When I was 13, I lost my grandfather to a sile...    0.435699   
3334  I wrote a letter last week talking about the w...    0.084276   
17    It was a fantastic new pink suit with big butt...    0.000109   
1453  Why do cats do that? They're cute, they're lov...    0.274083   
149   I am obsessed with forming healthy communities...    0.014482   
807   When I tell people that I'm trying to develop ...    0.255862   
1928  (Music) This is the human test, a test to see ...    0.319473   
...                                                 ...         ...   
1352  Every weekend for as long as I can remember, m...    0.158394   
679   2,300 years ago, the rulers of Alexandria set ...    0.000241   
1652  For the past decade, I've been studying non-st...    0.000211   
2472  As you might imagine, I'm absolutely passionat...    0.173579   
3280  The first half of the 20th century was an abso...    0.000100   
1128  When Reverend Jim Jones founded the Peoples Te...    0.308764   
1925  What do you think of when I say the word "desi...    0.060789   
2320  As any current or past geometry student knows,...    0.207900   
1071  I'm Chetan Bhatt and when I give my name, I'm ...    0.137798   
3148  Namaste. Salaam. Shalom. Sat Sri Akal. Greetin...    0.112999   
67    The drive through the world's most secure pris...    0.253755   
2651  How can I speak in 10 minutes about the bonds ...    0.080534   
2514  Now, I don't usually like cartoons, I don't th...    0.127681   
2723  So that's Johnny Depp, of course. And that's J...    0.556829   
3393  I grew up in Europe, and World War II caught m...    0.365957   
2230  If you wake up one morning with 1,000 times th...    0.048263   
31    For the past 15 years I've been trying to chan...    0.267776   
1279  I'm going to talk a little bit about where tec...    0.102067   
2639  What do I know that would cause me, a reticent...    0.029766   
840   A whip-like straw. Powerful, crushing blades. ...    0.130443   
610   Five years ago, I stood on the TED stage, and ...    0.217677   
3225  Take a look at this picture. It poses a very f...    0.000070   
570   We live in a medication nation. 4.5 billion dr...    0.308430   
3377  So, about three years ago I was in London, and...    0.138690   
343   Have you ever tried to understand a teenager? ...    0.434995  

In [331]:
topics_test_df.to_csv('test_data_with_topics.csv')

# LDA (n = 13)

In [35]:
lda_cv_13 = LatentDirichletAllocation(n_components=13,           # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=42,          # Random state
                                      batch_size=100,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      )

In [36]:
lda_cv_13.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=13, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [39]:
topic_top_words(lda_cv_13, cv.get_feature_names(), 10)

1           2        3         4             5           6   \
Topic 0        brain        life  patient   disease          body      health   
Topic 1        water        city   energy     space         light       earth   
Topic 2   technology        cell    human  computer     different        kind   
Topic 3    political  government    power    medium     democracy        vote   
Topic 4      country     percent   change   company       problem       child   
Topic 5         tell        life    story       day          love      little   
Topic 6        robot         leg     body       arm      robotics        walk   
Topic 7         rope     anatomy   oyster   emperor  illustration         bce   
Topic 8       patent   algorithm      bee      gold         sloth      breast   
Topic 9     language        word     book     write          read       learn   
Topic 10   satellite       orbit   rocket    launch         space  spacecraft   
Topic 11        food       music   number     sound          play         let   
Topic 12       woman         sex   female      male           men      sexual   

               7          8               9           10  
Topic 0     human      study            tell      cancer  
Topic 1    planet   building             big       place  
Topic 2       new       data          system      little  
Topic 3       war   internet             law     country  
Topic 4      talk        new       community       today  
Topic 5      talk       feel             try        kind  
Topic 6   robotic    control           drone  autonomous  
Topic 7     roman  gladiator          infest    inflated  
Topic 8   failure   medicine  pharmaceutical     company  
Topic 9     speak     letter         example        text  
Topic 10  climber      earth      subsurface        ship  
Topic 11      eat     answer            hear       voice  
Topic 12      ice     insect            cave      specie

# LDA (n = 10)

In [37]:
lda_cv_10 = LatentDirichletAllocation(n_components=10,           # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=42,          # Random state
                                      batch_size=100,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      )

In [38]:
lda_cv_10.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=10, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [56]:
lda_cv_10_table, dominant_topic_10, secondary_topic_10 = print_dtm(lda_cv_10, dtm_cv_train)

In [40]:
topic_top_words(lda_cv_10, cv.get_feature_names(), 10)

1           2          3          4         5          6   \
Topic 0       brain     patient       body    disease      life     health   
Topic 1      energy        city      space      light     earth   building   
Topic 2  technology        kind  different      human  computer        new   
Topic 3   political  government     medium  democracy  internet       vote   
Topic 4     country       woman      child     change      talk  community   
Topic 5        tell        life        day       love     story     little   
Topic 6       water        food     animal     specie     ocean      plant   
Topic 7         ork        orld        kit        ore       ory     orking   
Topic 8     company     percent      money     dollar  business    problem   
Topic 9    language       music      sound       word   student       play   

                  7         8        9         10  
Topic 0        human    cancer    study      tell  
Topic 1       planet     build      big  universe  
Topic 2       system      data   little      cell  
Topic 3  information  election    power  politics  
Topic 4       family    school     live      life  
Topic 5         feel      talk      try       kid  
Topic 6         fish      tree      eat      live  
Topic 7       ortant    oyster     rape       com  
Topic 8       number       lot   market       let  
Topic 9        learn     voice  teacher      hear

# LDA Vis
## n = 25

In [ ]:
pyLDAvis.enable_notebook()
panel_lda_25 = pyLDAvis.sklearn.prepare(lda_cv, dtm_cv_train, cv, mds='tsne')
panel_lda_25

## n = 20

In [69]:
pyLDAvis.enable_notebook()
panel_lda_20 = pyLDAvis.sklearn.prepare(lda_cv, dtm_cv_train, cv, mds='tsne')
panel_lda_20

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
4      -10.878068   10.538728       1        1  21.839496
0      -60.884026  -75.591820       2        1  18.792099
5       -2.336119  -53.289074       3        1  15.575139
2      -61.385319  -12.914634       4        1  13.922198
17     -28.737743  126.296997       5        1   8.018652
1        1.066606 -123.552811       6        1   6.412314
14      45.140720   -7.947869       7        1   5.236950
9     -140.795975  -98.530548       8        1   2.439114
3       61.531681  -83.240562       9        1   1.959206
11     -72.563057 -140.396881      10        1   1.861482
19      15.984491   63.578186      11        1   1.576492
13    -160.851624   68.945145      12        1   0.837255
8       85.961830   51.922935      13        1   0.716419
6      -99.020836  109.936348      14        1   0.480569
18    -176.764130   -8.681684      15        1   0.187994
10    -117.189880  -37.420200      16        1   0.065640
12     108.829918  -22.946203      17        1   0.034730
16      47.588097  121.934814      18        1   0.020384
7     -106.467834   30.176889      19        1   0.014757
15     -50.613804   59.328842      20        1   0.009108, topic_info=      Category         Freq        Term        Total  loglift  logprob
12609  Default  2362.000000       space  2362.000000  30.0000  30.0000
4847   Default  2176.000000        face  2176.000000  29.0000  29.0000
10032  Default  2701.000000        play  2701.000000  28.0000  28.0000
14993  Default  4552.000000       woman  4552.000000  27.0000  27.0000
2003   Default  2527.000000        cell  2527.000000  26.0000  26.0000
6121   Default  1922.000000      health  1922.000000  25.0000  25.0000
6126   Default  2737.000000        hear  2737.000000  24.0000  24.0000
11790  Default  2973.000000      school  2973.000000  23.0000  23.0000
1458   Default  2698.000000        body  2698.000000  22.0000  22.0000
3277   Default  2700.000000        data  2700.000000  21.0000  21.0000
1896   Default  1907.000000        care  1907.000000  20.0000  20.0000
7590   Default  3594.000000       learn  3594.000000  19.0000  19.0000
5259   Default  2022.000000        food  2022.000000  18.0000  18.0000
12588  Default  1773.000000       sound  1773.000000  17.0000  17.0000
7416   Default  2963.000000         kid  2963.000000  16.0000  16.0000
9780   Default  3687.000000     percent  3687.000000  15.0000  15.0000
9689   Default  1474.000000     patient  1474.000000  14.0000  14.0000
2136   Default  4106.000000       child  4106.000000  13.0000  13.0000
2223   Default  2509.000000        city  2509.000000  12.0000  12.0000
15010  Default  2627.000000        word  2627.000000  11.0000  11.0000
7651   Default  5467.000000         let  5467.000000  10.0000  10.0000
3790   Default  1500.000000     disease  1500.000000   9.0000   9.0000
2976   Default  3819.000000     country  3819.000000   8.0000   8.0000
13018  Default  1791.000000     student  1791.000000   7.0000   7.0000
8702   Default  1241.000000       music  1241.000000   6.0000   6.0000
3548   Default  2752.000000      design  2752.000000   5.0000   5.0000
1837   Default  1103.000000      cancer  1103.000000   4.0000   4.0000
7127   Default  1182.000000    internet  1182.000000   3.0000   3.0000
5773   Default  1734.000000  government  1734.000000   2.0000   2.0000
7513   Default  1560.000000    language  1560.000000   1.0000   1.0000
...        ...          ...         ...          ...      ...      ...
6538   Topic20     0.009619        idea  4843.127070  -3.8256  -9.6218
9996   Topic20     0.009619       place  3983.342618  -3.6301  -9.6219
9536   Topic20     0.009614        pain   611.216464  -1.7563  -9.6224
5101   Topic20     0.009612        fire   701.101798  -1.8936  -9.6226
10452  Topic20     0.009609     problem  4313.720527  -3.7109  -9.6229
1742   Topic20     0.009608    business  1545.563738  

In [91]:
pyLDAvis.save_html(panel_lda_20, 'tm_20.html')

## n = 17

In [70]:
pyLDAvis.enable_notebook()
panel_lda_17 = pyLDAvis.sklearn.prepare(lda_cv_17, dtm_cv_train, cv, mds='tsne')
panel_lda_17

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=               x           y  topics  cluster       Freq
topic                                                   
4       2.972113  -13.786730       1        1  22.876553
0      -7.288966   86.150291       2        1  20.041586
5      38.049393   65.587624       3        1  17.831953
2     -42.227043    6.162611       4        1  12.801679
1     -63.238548  -41.294518       5        1   9.927901
14    -48.099060   56.473579       6        1   5.650984
8     -48.087841  120.044159       7        1   2.576560
9      17.708776  131.640900       8        1   2.564611
3      92.846191   -8.328438       9        1   1.799207
11     47.892864  -45.589878      10        1   1.411064
13     92.039185   50.145565      11        1   1.072933
6     -94.766495   15.104293      12        1   0.783613
16     -9.109381  -64.732552      13        1   0.280131
12    -94.606842   77.712318      14        1   0.268655
10     44.945538   14.845922      15        1   0.066146
15     -1.493484   35.842178      16        1   0.026229
7      71.312836  105.574364      17        1   0.020193, topic_info=      Category         Freq         Term        Total  loglift  logprob
14993  Default  4513.000000        woman  4513.000000  30.0000  30.0000
12609  Default  2375.000000        space  2375.000000  29.0000  29.0000
10032  Default  2713.000000         play  2713.000000  28.0000  28.0000
2513   Default  2543.000000      company  2543.000000  27.0000  27.0000
11790  Default  2950.000000       school  2950.000000  26.0000  26.0000
5259   Default  2013.000000         food  2013.000000  25.0000  25.0000
6126   Default  2741.000000         hear  2741.000000  24.0000  24.0000
7416   Default  2950.000000          kid  2950.000000  23.0000  23.0000
8229   Default  1678.000000          men  1678.000000  22.0000  22.0000
7590   Default  3586.000000        learn  3586.000000  21.0000  21.0000
3277   Default  2780.000000         data  2780.000000  20.0000  20.0000
1458   Default  2643.000000         body  2643.000000  19.0000  19.0000
12588  Default  1785.000000        sound  1785.000000  18.0000  18.0000
3790   Default  1494.000000      disease  1494.000000  17.0000  17.0000
1837   Default  1129.000000       cancer  1129.000000  16.0000  16.0000
8601   Default  1462.000000       mother  1462.000000  15.0000  15.0000
5676   Default  1544.000000         girl  1544.000000  14.0000  14.0000
6121   Default  1922.000000       health  1922.000000  13.0000  13.0000
2223   Default  2527.000000         city  2527.000000  12.0000  12.0000
13367  Default  6084.000000         talk  6084.000000  11.0000  11.0000
15010  Default  2616.000000         word  2616.000000  10.0000  10.0000
7651   Default  5458.000000          let  5458.000000   9.0000   9.0000
13018  Default  1777.000000      student  1777.000000   8.0000   8.0000
9780   Default  3674.000000      percent  3674.000000   7.0000   7.0000
8702   Default  1255.000000        music  1255.000000   6.0000   6.0000
8541   Default  1975.000000        money  1975.000000   5.0000   5.0000
3548   Default  2780.000000       design  2780.000000   4.0000   4.0000
3931   Default  1059.000000       doctor  1059.000000   3.0000   3.0000
2976   Default  3784.000000      country  3784.000000   2.0000   2.0000
3043   Default  4128.000000       create  4128.000000   1.0000   1.0000
...        ...          ...          ...          ...      ...      ...
907    Topic17     0.018265  audiovisual     3.965817   3.1271  -9.7768
5784   Topic17     0.018264   graciously     3.985077   3.1222  -9.7768
5334   Topic17     0.018265   fortyseven     4.000192   3.1184  -9.7768
7692   Topic17     0.018265  lifeordeath     4.026958   3.1118  -9.7768
11996  Topic17     0.018265     seminary     4.027972   3.1116  -9.7768
11417  Topic17     0.018265   revelatory     4.037228   3.1092  -9.7768
8273   Topic17     0.018264     metadata     4.037696   3.1091  -9.7768
7946   Topic17     0.018264       madeup     4.041935   3.1081  -9

In [89]:
pyLDAvis.save_html(panel_lda_17, 'tm_17.html')

## n = 16

In [140]:
pyLDAvis.enable_notebook()
panel_lda_16 = pyLDAvis.sklearn.prepare(lda_cv_16, dtm_cv_train, cv, mds='tsne')
panel_lda_16

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
4     -225.349854  113.708771       1        1  24.914810
5      -11.214129  210.724503       2        1  20.808497
0     -370.246948  298.926941       3        1  18.712089
2     -115.863266  418.656219       4        1  12.234271
1      -38.937935  -11.941959       5        1   7.896398
14    -468.892181   27.747469       6        1   7.635276
9      394.578949  -27.335003       7        1   1.866240
11     195.150314  102.077026       8        1   1.855944
3     -445.241516 -257.978210       9        1   1.344141
13     -54.327461 -242.647034      10        1   1.219927
8     -219.093063 -421.854706      11        1   0.625380
6      147.051407 -128.542709      12        1   0.548419
12    -249.556183 -122.286224      13        1   0.252925
10     295.431061 -302.292206      14        1   0.050054
15     209.292816  347.965088      15        1   0.018032
7       68.881561 -446.165314      16        1   0.017598, topic_info=      Category         Freq              Term        Total  loglift  logprob
14993  Default  4581.000000             woman  4581.000000  30.0000  30.0000
12609  Default  2369.000000             space  2369.000000  29.0000  29.0000
10032  Default  2708.000000              play  2708.000000  28.0000  28.0000
6121   Default  1953.000000            health  1953.000000  27.0000  27.0000
1458   Default  2656.000000              body  2656.000000  26.0000  26.0000
15010  Default  2675.000000              word  2675.000000  25.0000  25.0000
1936   Default  2082.000000              case  2082.000000  24.0000  24.0000
1896   Default  1924.000000              care  1924.000000  23.0000  23.0000
6126   Default  2744.000000              hear  2744.000000  22.0000  22.0000
8229   Default  1704.000000               men  1704.000000  21.0000  21.0000
5259   Default  2019.000000              food  2019.000000  20.0000  20.0000
9689   Default  1502.000000           patient  1502.000000  19.0000  19.0000
7590   Default  3589.000000             learn  3589.000000  18.0000  18.0000
3790   Default  1515.000000           disease  1515.000000  17.0000  17.0000
1486   Default  1980.000000              book  1980.000000  16.0000  16.0000
12588  Default  1789.000000             sound  1789.000000  15.0000  15.0000
15071  Default  2427.000000             write  2427.000000  14.0000  14.0000
7651   Default  5463.000000               let  5463.000000  13.0000  13.0000
5773   Default  1726.000000        government  1726.000000  12.0000  12.0000
2976   Default  3808.000000           country  3808.000000  11.0000  11.0000
7513   Default  1609.000000          language  1609.000000  10.0000  10.0000
9780   Default  3693.000000           percent  3693.000000   9.0000   9.0000
1837   Default  1139.000000            cancer  1139.000000   8.0000   8.0000
6538   Default  4836.000000              idea  4836.000000   7.0000   7.0000
3548   Default  2743.000000            design  2743.000000   6.0000   6.0000
8702   Default  1254.000000             music  1254.000000   5.0000   5.0000
10885  Default  1788.000000              read  1788.000000   4.0000   4.0000
5539   Default  1463.000000              game  1463.000000   3.0000   3.0000
2587   Default  2029.000000          computer  2029.000000   2.0000   2.0000
6906   Default  2058.000000       information  2058.000000   1.0000   1.0000
...        ...          ...               ...          ...      ...      ...
12745  Topic16     0.016963        springtime     4.075633   3.1634  -9.7132
5602   Topic16     0.016963       generically     4.082460   3.1617  -9.7132
11247  Topic16     0.016963          rephrase     4.084652   3.1612  -9.7131
8873   Topic16     0.016962   neuroscientific     4.086359   3.1607  -9.7132
11417  Topic16     0.016963        revelatory     4.094968   3.1586  -9.7132
13337  Topic16     0.016963      systemically     4.097141   3.1

In [142]:
pyLDAvis.save_html(panel_lda_16, 'tm_16.html')

## n = 15

In [143]:
pyLDAvis.enable_notebook()
panel_lda_15 = pyLDAvis.sklearn.prepare(lda_cv_15, dtm_cv_train, cv, mds='tsne')
panel_lda_15

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
4      114.344879  114.308296       1        1  24.587229
5      105.821045  -93.749626       2        1  21.145207
0     -138.334473   95.320763       3        1  15.451213
2       -7.436697  111.259697       4        1  14.386955
1     -207.550629 -105.472603       5        1   9.191159
14      52.817650   14.603765       6        1   5.360391
3      168.010849    6.806950       7        1   3.503946
6      -94.169601 -157.789551       8        1   1.682424
11    -122.849174  -39.059418       9        1   1.386937
13     -94.894264  195.408295      10        1   1.073169
9       24.927401 -180.464874      11        1   0.976302
12     -53.413467   26.832108      12        1   0.638341
8      -12.255850  -72.093201      13        1   0.525448
10    -224.217957   28.070581      14        1   0.073441
7       36.154255  209.427582      15        1   0.017837, topic_info=      Category         Freq             Term        Total  loglift  logprob
14993  Default  4531.000000            woman  4531.000000  30.0000  30.0000
12609  Default  2370.000000            space  2370.000000  29.0000  29.0000
15010  Default  2632.000000             word  2632.000000  28.0000  28.0000
10032  Default  2694.000000             play  2694.000000  27.0000  27.0000
6121   Default  1932.000000           health  1932.000000  26.0000  26.0000
5259   Default  2006.000000             food  2006.000000  25.0000  25.0000
6126   Default  2738.000000             hear  2738.000000  24.0000  24.0000
8229   Default  1684.000000              men  1684.000000  23.0000  23.0000
9689   Default  1505.000000          patient  1505.000000  22.0000  22.0000
1486   Default  1931.000000             book  1931.000000  21.0000  21.0000
7590   Default  3558.000000            learn  3558.000000  20.0000  20.0000
15071  Default  2397.000000            write  2397.000000  19.0000  19.0000
7513   Default  1563.000000         language  1563.000000  18.0000  18.0000
3790   Default  1507.000000          disease  1507.000000  17.0000  17.0000
12588  Default  1779.000000            sound  1779.000000  16.0000  16.0000
7651   Default  5456.000000              let  5456.000000  15.0000  15.0000
2223   Default  2514.000000             city  2514.000000  14.0000  14.0000
9780   Default  3673.000000          percent  3673.000000  13.0000  13.0000
1837   Default  1150.000000           cancer  1150.000000  12.0000  12.0000
10885  Default  1758.000000             read  1758.000000  11.0000  11.0000
3548   Default  2754.000000           design  2754.000000  10.0000  10.0000
11532  Default  1412.000000            robot  1412.000000   9.0000   9.0000
6538   Default  4836.000000             idea  4836.000000   8.0000   8.0000
2976   Default  3818.000000          country  3818.000000   7.0000   7.0000
3661   Default  5247.000000        different  5247.000000   6.0000   6.0000
8702   Default  1243.000000            music  1243.000000   5.0000   5.0000
1687   Default  3636.000000            build  3636.000000   4.0000   4.0000
2587   Default  1964.000000         computer  1964.000000   3.0000   3.0000
4665   Default  3178.000000          example  3178.000000   2.0000   2.0000
3931   Default  1061.000000           doctor  1061.000000   1.0000   1.0000
...        ...          ...              ...          ...      ...      ...
12745  Topic15     0.017163       springtime     4.065912   3.1640  -9.7150
8273   Topic15     0.017163         metadata     4.071974   3.1625  -9.7150
8873   Topic15     0.017163  neuroscientific     4.076455   3.1614  -9.7150
7946   Topic15     0.017163           madeup     4.081780   3.1601  -9.7150
14427  Topic15     0.017164         uptodate     4.086163   3.1591  -9.7149
5602   Topic15     0.017163      generically     4.086064   3.1590  -9.7150
3482   Topic15     0.017163           demote     4.093071   3.1573  -9.7150
11524  

In [72]:
pyLDAvis.save_html(panel_lda_15, 'tm_15.html')

## n = 13

In [71]:
pyLDAvis.enable_notebook()
panel_lda_13 = pyLDAvis.sklearn.prepare(lda_cv_13, dtm_cv_train, cv, mds='tsne')
panel_lda_13

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
5      -28.370157   75.716713       1        1  24.945189
4      140.525131  125.038422       2        1  24.687763
2      -15.713381   -6.499068       3        1  16.586956
0      -34.624741  168.429764       4        1  12.803361
1       66.229309    7.804511       5        1  12.305604
3       54.002045   90.614914       6        1   3.944435
11    -115.580109  108.730423       7        1   2.165773
9      156.040054   31.690395       8        1   1.071873
12      31.304781  -90.663383       9        1   0.654448
6      125.523102  -64.160110      10        1   0.553318
8     -110.481079   11.011040      11        1   0.149137
10      58.766029  183.607056      12        1   0.102143
7      -69.457687  -81.489365      13        1   0.029998, topic_info=      Category         Freq         Term        Total  loglift  logprob
14993  Default  4596.000000        woman  4596.000000  30.0000  30.0000
12609  Default  2373.000000        space  2373.000000  29.0000  29.0000
15010  Default  2637.000000         word  2637.000000  28.0000  28.0000
2513   Default  2404.000000      company  2404.000000  27.0000  27.0000
1458   Default  2574.000000         body  2574.000000  26.0000  26.0000
1486   Default  1928.000000         book  1928.000000  25.0000  25.0000
8229   Default  1709.000000          men  1709.000000  24.0000  24.0000
4141   Default  1743.000000        earth  1743.000000  23.0000  23.0000
9045   Default  3189.000000       number  3189.000000  22.0000  22.0000
7590   Default  3547.000000        learn  3547.000000  21.0000  21.0000
7513   Default  1562.000000     language  1562.000000  20.0000  20.0000
15071  Default  2394.000000        write  2394.000000  19.0000  19.0000
10032  Default  2702.000000         play  2702.000000  18.0000  18.0000
5259   Default  2016.000000         food  2016.000000  17.0000  17.0000
11532  Default  1170.000000        robot  1170.000000  16.0000  16.0000
14739  Default  1971.000000         walk  1971.000000  15.0000  15.0000
7651   Default  5485.000000          let  5485.000000  14.0000  14.0000
1742   Default  1534.000000     business  1534.000000  13.0000  13.0000
10885  Default  1755.000000         read  1755.000000  12.0000  12.0000
8541   Default  1916.000000        money  1916.000000  11.0000  11.0000
3661   Default  5262.000000    different  5262.000000  10.0000  10.0000
12588  Default  1798.000000        sound  1798.000000   9.0000   9.0000
3548   Default  2751.000000       design  2751.000000   8.0000   8.0000
1554   Default  3594.000000        brain  3594.000000   7.0000   7.0000
2976   Default  3806.000000      country  3806.000000   6.0000   6.0000
4665   Default  3196.000000      example  3196.000000   5.0000   5.0000
8702   Default  1262.000000        music  1262.000000   4.0000   4.0000
13367  Default  6087.000000         talk  6087.000000   3.0000   3.0000
6538   Default  4843.000000         idea  4843.000000   2.0000   2.0000
2829   Default  1580.000000      control  1580.000000   1.0000   1.0000
...        ...          ...          ...          ...      ...      ...
8436   Topic13     0.852938    misguided    11.099253   5.5458  -6.3289
3855   Topic13     0.857117      dissect    19.016774   5.0123  -6.3240
9291   Topic13     0.530288      orchard    26.266637   4.2092  -6.8041
7496   Topic13     0.050450        lance     4.131535   3.7064  -9.1566
12991  Topic13     0.026382        strew     3.051274   3.3612  -9.8049
7372   Topic13     0.026382        jumbo     3.617083   3.1911  -9.8049
1197   Topic13     0.026382   beekeeping     3.655214   3.1806  -9.8049
5784   Topic13     0.026382   graciously     3.802306   3.1411  -9.8049
9851   Topic13     0.026382      pertain     3.824074   3.1354  -9.8049
14489  Topic13     0.026382    validated     3.825642   3.1350  -9.8049
3245   Topic13     0.026382        daisy     3.860750   3.1259 

In [90]:
pyLDAvis.save_html(panel_lda_13, 'tm_13.html')

## n = 10

In [57]:
pyLDAvis.enable_notebook()
panel_lda_10 = pyLDAvis.sklearn.prepare(lda_cv_10, dtm_cv_train, cv, mds='tsne')
panel_lda_10

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=               x          y  topics  cluster       Freq
topic                                                  
5      32.420952   8.115230       1        1  23.376828
4       0.648955  71.707100       2        1  20.279798
2      71.019684   9.971006       3        1  16.050137
0       3.785981  33.185135       4        1  12.138519
1     -42.666500  -9.222070       5        1   9.815659
8      -3.621689 -43.526516       6        1   8.159729
6      -3.632402  -4.171708       7        1   4.831058
3     -36.584400  35.804413       8        1   2.957136
9      44.391380  50.615383       9        1   2.281404
7      40.235809 -31.591665      10        1   0.109732, topic_info=      Category         Freq         Term        Total  loglift  logprob
15010  Default  2634.000000         word  2634.000000  30.0000  30.0000
10032  Default  2710.000000         play  2710.000000  29.0000  29.0000
7513   Default  1564.000000     language  1564.000000  28.0000  28.0000
12588  Default  1808.000000        sound  1808.000000  27.0000  27.0000
7590   Default  3553.000000        learn  3553.000000  26.0000  26.0000
2513   Default  2504.000000      company  2504.000000  25.0000  25.0000
1554   Default  3599.000000        brain  3599.000000  24.0000  24.0000
14786  Default  2552.000000        water  2552.000000  23.0000  23.0000
13018  Default  1750.000000      student  1750.000000  22.0000  22.0000
8702   Default  1282.000000        music  1282.000000  21.0000  21.0000
5259   Default  2015.000000         food  2015.000000  20.0000  20.0000
5773   Default  1745.000000   government  1745.000000  19.0000  19.0000
553    Default  1703.000000       animal  1703.000000  18.0000  18.0000
2223   Default  2488.000000         city  2488.000000  17.0000  17.0000
6126   Default  2741.000000         hear  2741.000000  16.0000  16.0000
15071  Default  2381.000000        write  2381.000000  15.0000  15.0000
8541   Default  1980.000000        money  1980.000000  14.0000  14.0000
7705   Default  2629.000000        light  2629.000000  13.0000  13.0000
6906   Default  2072.000000  information  2072.000000  12.0000  12.0000
2976   Default  3780.000000      country  3780.000000  11.0000  11.0000
9780   Default  3728.000000      percent  3728.000000  10.0000  10.0000
9045   Default  3186.000000       number  3186.000000   9.0000   9.0000
3948   Default  1791.000000       dollar  1791.000000   8.0000   8.0000
7651   Default  5489.000000          let  5489.000000   7.0000   7.0000
4418   Default  1989.000000       energy  1989.000000   6.0000   6.0000
1486   Default  1905.000000         book  1905.000000   5.0000   5.0000
10127  Default  1044.000000    political  1044.000000   4.0000   4.0000
6538   Default  4834.000000         idea  4834.000000   3.0000   3.0000
8195   Default  1177.000000       medium  1177.000000   2.0000   2.0000
12609  Default  2382.000000        space  2382.000000   1.0000   1.0000
...        ...          ...          ...          ...      ...      ...
13708  Topic10    12.230132           tk    13.139214   6.7432  -4.9628
9514   Topic10    19.307850       oyster    20.743623   6.7432  -4.5062
9351   Topic10    11.359181          ort    12.263254   6.7383  -5.0367
9324   Topic10    10.966334        ories    11.870365   6.7357  -5.0719
9333   Topic10    10.782945        ority    11.687029   6.7344  -5.0887
9361   Topic10    10.757056         orts    11.661146   6.7342  -5.0911
9339   Topic10    10.711523          orm    11.615578   6.7339  -5.0954
2401   Topic10    10.623355        colla    11.527391   6.7332  -5.1036
9331   Topic10    10.180279        oring    11.084364   6.7298  -5.1463
9306   Topic10     9.543924        orest    10.448048   6.7244  -5.2108
9303   Topic10     8.341908         ords     9.246019   6.7120  -5.3454
9305   Topic10     8.072738         ored     8.976788   6.7087  -5.3782
9340   Topic10     7.782398     ormation     8.686497   6.7050  -5.4148
13155  Topic10     7.541663          sup     

# Prior Vis

In [170]:
pyLDAvis.enable_notebook()
panel = pyLDAvis.sklearn.prepare(lda_cv, dtm_cv_train, cv, mds='tsne')
panel

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
4      -10.878068   10.538728       1        1  21.841652
0      -60.884026  -75.591820       2        1  18.782615
5       -2.336119  -53.289074       3        1  15.579221
2      -61.385319  -12.914634       4        1  13.924153
17     -28.737743  126.296997       5        1   8.018799
1        1.066606 -123.552811       6        1   6.410817
14      45.140720   -7.947869       7        1   5.237531
9     -140.795975  -98.530548       8        1   2.438570
3       61.531681  -83.240562       9        1   1.959782
11     -72.563057 -140.396881      10        1   1.861380
19      15.984491   63.578186      11        1   1.577301
13    -160.851624   68.945145      12        1   0.837344
8       85.961830   51.922935      13        1   0.716142
6      -99.020836  109.936348      14        1   0.481855
18    -176.764130   -8.681684      15        1   0.188131
10    -117.189880  -37.420200      16        1   0.065641
12     108.829918  -22.946203      17        1   0.034817
16      47.588097  121.934814      18        1   0.020385
7     -106.467834   30.176889      19        1   0.014756
15     -50.613804   59.328842      20        1   0.009108, topic_info=      Category         Freq        Term        Total  loglift  logprob
12609  Default  2362.000000       space  2362.000000  30.0000  30.0000
4847   Default  2176.000000        face  2176.000000  29.0000  29.0000
10032  Default  2701.000000        play  2701.000000  28.0000  28.0000
14993  Default  4552.000000       woman  4552.000000  27.0000  27.0000
2003   Default  2527.000000        cell  2527.000000  26.0000  26.0000
6121   Default  1922.000000      health  1922.000000  25.0000  25.0000
6126   Default  2737.000000        hear  2737.000000  24.0000  24.0000
3277   Default  2700.000000        data  2700.000000  23.0000  23.0000
11790  Default  2972.000000      school  2972.000000  22.0000  22.0000
1458   Default  2698.000000        body  2698.000000  21.0000  21.0000
1896   Default  1907.000000        care  1907.000000  20.0000  20.0000
7590   Default  3594.000000       learn  3594.000000  19.0000  19.0000
5259   Default  2023.000000        food  2023.000000  18.0000  18.0000
12588  Default  1773.000000       sound  1773.000000  17.0000  17.0000
7416   Default  2963.000000         kid  2963.000000  16.0000  16.0000
9780   Default  3687.000000     percent  3687.000000  15.0000  15.0000
9689   Default  1474.000000     patient  1474.000000  14.0000  14.0000
2136   Default  4106.000000       child  4106.000000  13.0000  13.0000
2223   Default  2509.000000        city  2509.000000  12.0000  12.0000
15010  Default  2627.000000        word  2627.000000  11.0000  11.0000
3790   Default  1500.000000     disease  1500.000000  10.0000  10.0000
7651   Default  5467.000000         let  5467.000000   9.0000   9.0000
2976   Default  3819.000000     country  3819.000000   8.0000   8.0000
13018  Default  1791.000000     student  1791.000000   7.0000   7.0000
8702   Default  1241.000000       music  1241.000000   6.0000   6.0000
3548   Default  2752.000000      design  2752.000000   5.0000   5.0000
1837   Default  1103.000000      cancer  1103.000000   4.0000   4.0000
7127   Default  1182.000000    internet  1182.000000   3.0000   3.0000
5773   Default  1734.000000  government  1734.000000   2.0000   2.0000
7513   Default  1560.000000    language  1560.000000   1.0000   1.0000
...        ...          ...         ...          ...      ...      ...
6538   Topic20     0.009619        idea  4843.167015  -3.8256  -9.6218
9996   Topic20     0.009619       place  3983.370406  -3.6301  -9.6219
9536   Topic20     0.009614        pain   611.151850  -1.7562  -9.6224
5101   Topic20     0.009612        fire   701.104419  -1.8936  -9.6226
10452  Topic20     0.009609     problem  4313.729268  -3.7109  -9.6229
1742   Topic20     0.009608    business  1545.613164  

In [185]:
panel_ = pyLDAvis.sklearn.prepare(lda_cv, dtm_cv_train, cv)
panel_

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
4      0.150229  0.088887       1        1  21.841652
0      0.135292  0.093346       2        1  18.782615
5      0.167801  0.115149       3        1  15.579221
2      0.140050  0.061241       4        1  13.924153
17     0.130429  0.064695       5        1   8.018799
1      0.178770  0.065837       6        1   6.410817
14     0.149095  0.069250       7        1   5.237531
9      0.203998 -0.004789       8        1   2.438570
3      0.129053 -0.013374       9        1   1.959782
11     0.093458 -0.185219      10        1   1.861380
19     0.041769 -0.210230      11        1   1.577301
13     0.028262 -0.093494      12        1   0.837344
8     -0.089301 -0.370828      13        1   0.716142
6     -0.086336 -0.084647      14        1   0.481855
18    -0.217370 -0.042193      15        1   0.188131
10    -0.251153  0.072521      16        1   0.065641
12    -0.238712  0.087704      17        1   0.034817
16    -0.229126  0.092839      18        1   0.020385
7     -0.222056  0.095352      19        1   0.014756
15    -0.214152  0.097953      20        1   0.009108, topic_info=      Category         Freq        Term        Total  loglift  logprob
12609  Default  2362.000000       space  2362.000000  30.0000  30.0000
4847   Default  2176.000000        face  2176.000000  29.0000  29.0000
10032  Default  2701.000000        play  2701.000000  28.0000  28.0000
14993  Default  4552.000000       woman  4552.000000  27.0000  27.0000
2003   Default  2527.000000        cell  2527.000000  26.0000  26.0000
6121   Default  1922.000000      health  1922.000000  25.0000  25.0000
6126   Default  2737.000000        hear  2737.000000  24.0000  24.0000
3277   Default  2700.000000        data  2700.000000  23.0000  23.0000
11790  Default  2972.000000      school  2972.000000  22.0000  22.0000
1458   Default  2698.000000        body  2698.000000  21.0000  21.0000
1896   Default  1907.000000        care  1907.000000  20.0000  20.0000
7590   Default  3594.000000       learn  3594.000000  19.0000  19.0000
5259   Default  2023.000000        food  2023.000000  18.0000  18.0000
12588  Default  1773.000000       sound  1773.000000  17.0000  17.0000
7416   Default  2963.000000         kid  2963.000000  16.0000  16.0000
9780   Default  3687.000000     percent  3687.000000  15.0000  15.0000
9689   Default  1474.000000     patient  1474.000000  14.0000  14.0000
2136   Default  4106.000000       child  4106.000000  13.0000  13.0000
2223   Default  2509.000000        city  2509.000000  12.0000  12.0000
15010  Default  2627.000000        word  2627.000000  11.0000  11.0000
3790   Default  1500.000000     disease  1500.000000  10.0000  10.0000
7651   Default  5467.000000         let  5467.000000   9.0000   9.0000
2976   Default  3819.000000     country  3819.000000   8.0000   8.0000
13018  Default  1791.000000     student  1791.000000   7.0000   7.0000
8702   Default  1241.000000       music  1241.000000   6.0000   6.0000
3548   Default  2752.000000      design  2752.000000   5.0000   5.0000
1837   Default  1103.000000      cancer  1103.000000   4.0000   4.0000
7127   Default  1182.000000    internet  1182.000000   3.0000   3.0000
5773   Default  1734.000000  government  1734.000000   2.0000   2.0000
7513   Default  1560.000000    language  1560.000000   1.0000   1.0000
...        ...          ...         ...          ...      ...      ...
6538   Topic20     0.009619        idea  4843.167015  -3.8256  -9.6218
9996   Topic20     0.009619       place  3983.370406  -3.6301  -9.6219
9536   Topic20     0.009614        pain   611.151850  -1.7562  -9.6224
5101   Topic20     0.009612        fire   701.104419  -1.8936  -9.6226
10452  Topic20     0.009609     problem  4313.729268  -3.7109  -9.6229
1742   Topic20     0.009608    business  1545.613164  -2.6845  -9.6229
5562   Topic20     0.009607         gas   565.867516  -1.6798  -9.6231


# LDA (n = 15)

In [187]:
lda_cv_15 = LatentDirichletAllocation(n_components=15,           # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=42,          # Random state
                                      batch_size=100,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      )

In [188]:
lda_cv_15.fit(dtm_cv_train)

LatentDirichletAllocation(batch_size=100, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=15, n_jobs=-1,
                          perp_tol=0.1, random_state=42, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [191]:
display_topics(lda_cv_15, cv.get_feature_names(), 15)

Topic 0:
life tell brain human talk feel experience study ask person happen question mean try child
Topic 1:
light energy earth planet space universe big water car life mean kind little star carbon
Topic 2:
cell brain human technology system different new data computer little body kind able information animal
Topic 3:
political government power medium war democracy country vote internet politics election information law citizen religion
Topic 4:
country percent change company problem new talk today lot happen money let community big child
Topic 5:
day tell story life love little kid talk feel try ask school kind learn child
Topic 6:
robot machine computer build game leg ant intelligence control try car fly problem number design
Topic 7:
socket tk amputate prosthesis amputee dandy leone sierra emperor fusiform gyrus edi blister government problem
Topic 8:
patient cancer health disease doctor medicine medical treatment tumor surgery breast patent bee cure physician
Topic 9:
language word

In [192]:
pyLDAvis.enable_notebook()
panel_15 = pyLDAvis.sklearn.prepare(lda_cv_15, dtm_cv_train, cv, mds='tsne')
panel_15

//anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=                x           y  topics  cluster       Freq
topic                                                    
4      114.344879  114.308296       1        1  24.591027
5      105.821045  -93.749626       2        1  21.056523
0     -138.334473   95.320763       3        1  15.522716
2       -7.436697  111.259697       4        1  14.491121
1     -207.550629 -105.472603       5        1   9.132694
14      52.817650   14.603765       6        1   5.329329
3      168.010849    6.806950       7        1   3.529686
6      -94.169601 -157.789551       8        1   1.601510
11    -122.849174  -39.059418       9        1   1.387052
13     -94.894264  195.408295      10        1   1.079350
9       24.927401 -180.464874      11        1   0.980557
12     -53.413467   26.832108      12        1   0.635098
8      -12.255850  -72.093201      13        1   0.570811
10    -224.217957   28.070581      14        1   0.074720
7       36.154255  209.427582      15        1   0.017807, topic_info=      Category         Freq             Term        Total  loglift  logprob
14993  Default  4460.000000            woman  4460.000000  30.0000  30.0000
12609  Default  2365.000000            space  2365.000000  29.0000  29.0000
15010  Default  2634.000000             word  2634.000000  28.0000  28.0000
10032  Default  2695.000000             play  2695.000000  27.0000  27.0000
6121   Default  1926.000000           health  1926.000000  26.0000  26.0000
5259   Default  2007.000000             food  2007.000000  25.0000  25.0000
8229   Default  1663.000000              men  1663.000000  24.0000  24.0000
6126   Default  2739.000000             hear  2739.000000  23.0000  23.0000
1486   Default  1932.000000             book  1932.000000  22.0000  22.0000
9689   Default  1488.000000          patient  1488.000000  21.0000  21.0000
7590   Default  3561.000000            learn  3561.000000  20.0000  20.0000
15071  Default  2398.000000            write  2398.000000  19.0000  19.0000
7513   Default  1564.000000         language  1564.000000  18.0000  18.0000
3790   Default  1501.000000          disease  1501.000000  17.0000  17.0000
12588  Default  1780.000000            sound  1780.000000  16.0000  16.0000
7651   Default  5456.000000              let  5456.000000  15.0000  15.0000
2223   Default  2514.000000             city  2514.000000  14.0000  14.0000
9780   Default  3673.000000          percent  3673.000000  13.0000  13.0000
10885  Default  1759.000000             read  1759.000000  12.0000  12.0000
3548   Default  2753.000000           design  2753.000000  11.0000  11.0000
1837   Default  1128.000000           cancer  1128.000000  10.0000  10.0000
11532  Default  1384.000000            robot  1384.000000   9.0000   9.0000
6538   Default  4835.000000             idea  4835.000000   8.0000   8.0000
3661   Default  5249.000000        different  5249.000000   7.0000   7.0000
2976   Default  3817.000000          country  3817.000000   6.0000   6.0000
8702   Default  1245.000000            music  1245.000000   5.0000   5.0000
1687   Default  3634.000000            build  3634.000000   4.0000   4.0000
4665   Default  3179.000000          example  3179.000000   3.0000   3.0000
3931   Default  1057.000000           doctor  1057.000000   2.0000   2.0000
5914   Default  2565.000000             grow  2565.000000   1.0000   1.0000
...        ...          ...              ...          ...      ...      ...
8873   Topic15     0.017137  neuroscientific     4.078457   3.1611  -9.7147
7946   Topic15     0.017137           madeup     4.080301   3.1607  -9.7147
5602   Topic15     0.017138      generically     4.081426   3.1604  -9.7147
3482   Topic15     0.017137           demote     4.095788   3.1569  -9.7147
11524  Topic15     0.017137          roadway     4.106848   3.1542  -9.7147
13337  Topic15     0.017137     systemically     4.121787   3.1506  -9.7147
2698   Topic15     0.017137         connects     4.126271   3.1495  -9.7147
13622  

# GridSearch LDA

In [171]:
# Define Search Param
search_params = {'n_components': [15, 20, 25], 'learning_decay': [.5, .7, .9]}

# Init the Model
lda = LatentDirichletAllocation(max_iter = 5, 
                                learning_method = 'online', 
                                random_state = 42, 
                                batch_size = 100, 
                                evaluate_every = -1, 
                                n_jobs = -1)

In [172]:
# Init Grid Search Class
model = GridSearchCV(lda, param_grid=search_params)

# Do the Grid Search
model.fit(dtm_cv_train)

GridSearchCV(cv=None, error_score=nan,
             estimator=LatentDirichletAllocation(batch_size=100,
                                                 doc_topic_prior=None,
                                                 evaluate_every=-1,
                                                 learning_decay=0.7,
                                                 learning_method='online',
                                                 learning_offset=10.0,
                                                 max_doc_update_iter=100,
                                                 max_iter=5,
                                                 mean_change_tol=0.001,
                                                 n_components=10, n_jobs=-1,
                                                 perp_tol=0.1, random_state=42,
                                                 topic_word_prior=None,
                                                 total_samples=1000000.0,
                                

In [174]:
# Best Model
best_lda_model = model.best_estimator_

# Model Parameters
print("Best Model's Params: ", model.best_params_)

# Log Likelihood Score
print("Best Log Likelihood Score: ", model.best_score_)

# Perplexity
print("Model Perplexity: ", best_lda_model.perplexity(dtm_cv_train))

Best Model's Params:  {'learning_decay': 0.5, 'n_components': 15}
Best Log Likelihood Score:  -2663245.809228584
Model Perplexity:  2729.5166491392133


In [183]:
lda_cv.score(dtm_cv_train)

-12588505.9196547

In [184]:
lda_cv.perplexity(dtm_cv_train)

2694.0187784956825

In [180]:
model.cv_results_

{'mean_fit_time': array([31.29911532, 36.14828281, 41.87749352, 35.78892303, 36.5821672 ,
        44.91563559, 33.91294436, 36.47420406, 42.02768722]),
 'std_fit_time': array([2.64034123, 0.48089545, 2.28763294, 1.90581123, 2.04208753,
        3.15282506, 2.21647108, 1.17721809, 1.10350948]),
 'mean_score_time': array([0.45925689, 0.66473627, 0.52204843, 0.57197323, 0.56140862,
        0.77946038, 0.52758923, 0.67964816, 0.66788373]),
 'std_score_time': array([0.06798872, 0.10029592, 0.02519988, 0.07459057, 0.06073278,
        0.1724118 , 0.03105565, 0.07978363, 0.09849965]),
 'param_learning_decay': masked_array(data=[0.5, 0.5, 0.5, 0.7, 0.7, 0.7, 0.9, 0.9, 0.9],
              mask=[False, False, False, False, False, False, False, False,
                    False],
        fill_value='?',
             dtype=object),
 'param_n_components': masked_array(data=[15, 20, 25, 15, 20, 25, 15, 20, 25],
              mask=[False, False, False, False, False, False, False, False,
                

In [175]:
# Get Log Likelyhoods from Grid Search Output
n_topics = [15, 20, 25]
log_likelyhoods_5 = [round(gscore.mean_validation_score) for gscore in model.grid_scores_ if gscore.parameters['learning_decay']==0.5]
log_likelyhoods_7 = [round(gscore.mean_validation_score) for gscore in model.grid_scores_ if gscore.parameters['learning_decay']==0.7]
log_likelyhoods_9 = [round(gscore.mean_validation_score) for gscore in model.grid_scores_ if gscore.parameters['learning_decay']==0.9]

# Show graph
plt.figure(figsize=(12, 8))
plt.plot(n_topics, log_likelyhoods_5, label='0.5')
plt.plot(n_topics, log_likelyhoods_7, label='0.7')
plt.plot(n_topics, log_likelyhoods_9, label='0.9')
plt.title("Choosing Optimal LDA Model")
plt.xlabel("Num Topics")
plt.ylabel("Log Likelyhood Scores")
plt.legend(title='Learning decay', loc='best')
plt.show()

AttributeError: 'GridSearchCV' object has no attribute 'grid_scores_'